In [ ]:
import glob
import numpy as np
import cv2
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd
import os
import re
from scipy import signal
from scipy import stats
from scipy import optimize, interpolate
import statistics

plt.rcParams['pdf.fonttype'] = 42


In [ ]:
# 各strainのデータを読み込む
df_tot_CDK2 = pd.read_csv("_data_to_plot_asym_timecourse.csv")
df_tot_CDK = pd.DataFrame({})
cells = df_tot_CDK2['cell'].unique().tolist()
for cell in cells:
    df_temp = df_tot_CDK2.loc[df_tot_CDK2["cell"] == cell]
    df_temp["time"] = df_temp["time"] - df_temp["time"].to_list()[-1]
    df_tot_CDK = pd.concat([df_tot_CDK, df_temp])
print(df_tot_CDK)
    

In [ ]:
def detect_min_frame(vs):
    diffs = []
    for i in range(len(vs) - 1):
        diffs.append(vs[i+1] - vs[i])
    min_frame = np.argmin(diffs)   # 傾きが一番小さいところ（落ちる直前）
    return min_frame, diffs

def change_point_detection_max_slope(ts, ratios, w=4):
    n_time = len(ts)
    diffs = np.zeros((n_time,))
    for i in range(n_time - w):
        beta, _ = np.polyfit(ts[i:i+w], ratios[i:i+w], deg=1)
        diffs[i] = beta
    frame_change = np.argmax(diffs)
    max_dif = max(diffs)
    med = statistics.median(diffs)
    frame_change2 = np.where(diffs > (med+max_dif)/2)[0][0]
    return frame_change, frame_change2, diffs


#
# piecewise linear regression
#
def piecewise_linear_two_segments(x, x0, y0, b0, b1):
    return np.piecewise(x, [x <= x0, x > x0], [lambda x: b0*(x - x0) + y0, lambda x: b1*(x - x0) + y0])

def piecewise_linear_three_segments(x, x0, x1, y0, b0, b1, b2):
    return np.piecewise(x, [x <= x0, np.logical_and(x0 < x, x <= x0 + x1), x0 + x1 < x], [lambda x: b0*(x - x0) + y0, lambda x: b1*(x-x0) + y0, lambda x: b2*(x - x0 - x1) + b1*(x - x0) + y0])

def initial_guess2(ts):
    rmin = 1.3
    rmax = 2.2
    tmin = ts[0]
    tmax = ts[-1]
    #p0_2 = [0.5*tmin, 1.6, 0., 0.]
    #bounds2 = ([tmin, rmin, 0.0, 0.0], [0, rmax, 0.1, 0.1])
    p0_2 = [0.5*(tmin + tmax), 1.6, 0., 0.]
    bounds2 = ([tmin, rmin, 0.0, 0.0], [tmax, rmax, 0.1, 0.1])
    return p0_2, bounds2

def initial_guess3(ts, p2):
    rmin = 1.3
    rmax = 2.2
    tmin = ts[0]
    tmax = ts[-1]
    p0_3 = [p2[0], 10, p2[1], p2[2], p2[2], p2[3]]
    bounds3 = ([tmin, 0, rmin, 0.0, 0.0, 0.0], [tmax, 200, rmax, 0.1, 0.1, 0.1])
    return p0_3, bounds3



ratio_drops = []
ratio_peaks = []
ratio_cps = []
cyc_peaks = []
cells_plt = []
strains_plt = []
ratio_cps_value = []
ratio_peaks_value = []
ratio_cyclin_value = []
ratio_cyclin_value2 = []
for strain in strains:
    df_strain = df_tot_CDK.loc[df_tot_CDK["SL"]==strain]
    cells = df_strain['cell'].unique().tolist()
    cells_to_omit = omit_dict[strain]

    CDK_peaks = []
    cell_ids = []
    n_cells = len(cells)
    print('strain: ', strain, ', # of cells: ', n_cells)
    
    change_points_max_slope = np.zeros((n_cells,))

    for cell in cells:
        if int(cell) in cells_to_omit:
            continue

        df = df_strain.loc[df_strain["cell"] == cell]
        ts = df["time"].astype(float).tolist()
        rs = df["ratio"].tolist()
        rs = np.convolve(rs, [1, 1, 1], mode="same")/3
        rs[0] = rs[1]
        rs[-1] = rs[-2]
        cs = df["RFP"].tolist()
        cs = np.convolve(cs, [1, 1, 1], mode="same")/3
        cs[0] = cs[1]
        cs[-1] = cs[-2]

        min_frame_ratio, _ = detect_min_frame(rs)
        peak_frame_ratio = np.argmax(rs)
        peak_frame_cyc = np.argmax(cs)

        w1 = 5
        w2 = peak_frame_ratio
        p0_twoseg, bounds_twoseg = initial_guess2(ts[w1:w2])
        p2, _ = optimize.curve_fit(piecewise_linear_two_segments, ts[w1:w2], rs[w1:w2], p0=p0_twoseg, bounds=bounds_twoseg)
        p0_threeseg, bounds_threeseg = initial_guess3(ts[w1:w2], p2)
        p3, _ = optimize.curve_fit(piecewise_linear_three_segments, ts[w1:w2], rs[w1:w2], p0=p0_threeseg, bounds=bounds_threeseg)
        
        ratio_drops.append(ts[min_frame_ratio])
        ratio_peaks.append(ts[peak_frame_ratio])
        cyc_peaks.append(ts[peak_frame_cyc])
        cells_plt.append(cell)
        strains_plt.append(strain)
        ratio_cyclin_value.append(rs[peak_frame_cyc])
        ratio_peaks_value.append(rs[peak_frame_ratio])
        if strain == "HS115":
            ratio_cps.append(p3[0] + p3[1])
            ratio_cps_value.append(float(piecewise_linear_three_segments(p3[0] + p3[1], *p3)))
        else:
            ratio_cps.append(p2[0])
            ratio_cps_value.append(float(piecewise_linear_two_segments(p2[0], *p2)))
            
df_time_plot = pd.DataFrame({})
df_time_plot["ratio_drop"] = ratio_drops
df_time_plot["ratio_peak"] = ratio_peaks
df_time_plot["cyclin_peak"] = cyc_peaks
df_time_plot["ratio_cp"] = ratio_cps
df_time_plot["cell"] = cells_plt
df_time_plot["strain"] = strains_plt

df_CDK_plot = pd.DataFrame({})
df_CDK_plot["CDKatCP"] = ratio_cps_value
df_CDK_plot["CDKatCyc"] = ratio_cyclin_value
df_CDK_plot["CDKatPeak"] = ratio_peaks_value
df_CDK_plot["cell"] = cells_plt
df_CDK_plot["strain"] = strains_plt


In [ ]:
#display(df_CDK_plot)
fig, axes = plt.subplots(1, 3, figsize=(12, 6))
sns.swarmplot(x="strain", y="CDKatCP", data=df_CDK_plot, order=order, s=8, ax=axes[0])
sns.boxplot(x="strain", y="CDKatCP", data=df_CDK_plot, order=order, color="white", ax=axes[0])
sns.swarmplot(x="strain", y="CDKatCyc", data=df_CDK_plot, order=order, s=8, ax=axes[1])
sns.boxplot(x="strain", y="CDKatCyc", data=df_CDK_plot, order=order, color="white", ax=axes[1])
sns.swarmplot(x="strain", y="CDKatPeak", data=df_CDK_plot, order=order, s=8, ax=axes[2])
sns.boxplot(x="strain", y="CDKatPeak", data=df_CDK_plot, order=order, color="white", ax=axes[2])
axes[0].set_ylim([1.4, 2.2])
axes[1].set_ylim([1.4, 2.2])
axes[2].set_ylim([1.4, 2.2])
plt.savefig("./_CDKactivity_at_events.png")
plt.savefig("./_CDKactivity_at_events.pdf")
short = df_CDK_plot.loc[df_CDK_plot["strain"]=="short"]["CDKatCP"]
long = df_CDK_plot.loc[df_CDK_plot["strain"]=="long"]["CDKatCP"]
t, p = stats.ttest_ind(short, long, equal_var=False)
print("short vs long", t, p)
short = df_CDK_plot.loc[df_CDK_plot["strain"]=="short"]["CDKatCyc"]
long = df_CDK_plot.loc[df_CDK_plot["strain"]=="long"]["CDKatCyc"]
t, p = stats.ttest_ind(short, long, equal_var=False)
print("short vs long", t, p)
short = df_CDK_plot.loc[df_CDK_plot["strain"]=="short"]["CDKatPeak"]
long = df_CDK_plot.loc[df_CDK_plot["strain"]=="long"]["CDKatPeak"]
t, p = stats.ttest_ind(short, long, equal_var=False)
print("short vs long", t, p)

